In [1]:
import numpy as np
import pandas as pd
import sqlite3
from nltk import SnowballStemmer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.cluster import KMeans
from sklearn.metrics import pairwise_distances_argmin_min
from sklearn import manifold
#from cuml.manifold import TSNE
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
from gensim.models.keyedvectors import KeyedVectors
from tqdm import tqdm
from nltk import word_tokenize


In [2]:
data = pd.read_csv('data_featuring.txt', sep='|')
wordvectors_file_vec = 'embeddings-s-model.vec'
cantidad = 100000
wordvectors = KeyedVectors.load_word2vec_format(wordvectors_file_vec, limit=cantidad)

In [3]:
data

titulo  \
0       Cerca de ocho toneladas de coca del Clan del G...   
1       Capturado alias ‘Arturo’, segundo cabecilla de...   
2       Explicaron el traslado de cuerpos posiblemente...   
3       Sigue la guerra verde: ataque a familia de esm...   
4       Investigan caso de recluso amarrado y golpeado...   
...                                                   ...   
100635   Hallan cuerpo de turista que cayó al río Saldaña   
100636  Desmantelan Bacrim dentro del Ejército en el T...   
100637  Continúa ola delincuencial en Mariquita: Asesi...   
100638             Arteaga fue hallado en el río Chipalo    
100639  Dos motociclistas mueren en accidentes de trán...   

                                                   cuerpo  \
0       En una operación de la Policía Nacional y la A...   
1       Sería el encargado de organizar esta estructur...   
2       Hace unos días la ‘Ciudad de las Acacias’ cono...   
3       Familiares de Fray Genaro Cortés Salinas, el c...   
4       Aún se trata de esclarecer las circunstancias ...   
...                                                   ...   
100635  Mediante intensas búsquedas por parte de los o...   
100636  Mediante la operación militar denominada Troya...   
100637  Los hechos se registraron en horas de la tarde...   
100638  Consternado quedó uno de los habitantes de la ...   
100639  Con una buseta El primer caso ocurrió en el ki...   

          fecha_publicacion          diario  \
0       2020-07-01 17:43:00  diariodelcauca   
1       2020-07-01 18:40:00  diariodelcauca   
2       2020-07-01 18:42:00  diariodelcauca   
3       2020-07-01 19:21:00  diariodelcauca   
4       2020-07-02 08:42:00  diariodelcauca   
...                     ...             ...   
100635  2012-03-20 13:45:00      elnuevodia   
100636  2012-03-15 14:40:00      elnuevodia   
100637  2012-03-17 04:00:00      elnuevodia   
100638  2012-04-27 04:00:00      elnuevodia   
100639  2012-03-19 04:03:00      elnuevodia   

                                                      url  page  year  month  \
0       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
1       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
2       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
3       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
4       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
...                                                   ...   ...   ...    ...   
100635  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100636  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100637  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100638  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      4   
100639  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   

        week                                                 id  long_cuerpo  \
0         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          225   
1         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          420   
2         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          488   
3         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          371   
4         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          145   
...      ...                                                ...          ...   
100635    12  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          359   
100636    11  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...         1156   
100637    11  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          292   
100638    17  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          328   
100639    12  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          266   

                                           pre_clean_text  \
0       cerca ocho toneladas coca cla

In [5]:
#Hecho contra la población civil
categoria0 = [
                "homicidio",
                 "masacre", 
                 "secuestro",
                 "tortura",
                 "desplazamiento",
                 "forzado",
                 "confinamiento",
                 "accidente",
                 "mina",
#                 "antipersona",
                 "atentado",
                 "reclutamiento",
                 "violencia",
                 "sexual",
                 "ataque",
                 "indiscriminado",
                 "bienes",
                 "civiles"
]

#acciones armadas
categoria1 = [
                "combate",
                "enfrentamiento",
                "hostigamiento",
                "emboscada",
                "acto",
                "terrorismo",
                "ataque",
                "instalación",
                "militar",
                "policía" ,
                "restricción",
                "movilidad", 
                "retenes",
                "ilegal", 
                "paro",
                "armado",
                "indiscriminado",
                "incursión",
                "población"
]

# Acciones institucionales
categoria2 = [
                "captura",
                "desactivación",
                "artefacto",
                "explosivo",
#                "antinarcotico",
                "incautación",
                "rescate",
                "secuestrado",
                "liberación",
                "misión",
                "humanitaria"
]

#Otro tipo de evento
categoria3 = [
                "pronunciamiento",
                "organismo",
                "internacional",
                "nacional",
                "conflicto",
                "derecho",
                "humano",
                "ddhh",
                "victimización"
]

In [5]:
def similitud_categorias(palabras):
    sim0 = []
    sim1 = []
    sim2 = []
    sim3 = []
    not_in_we = []
    for w_n in palabras:
        for w in categoria0:
            try:
                sim0.append(wordvectors.similarity(w_n, w))
            except:
                not_in_we.append(w_n)

        for w in categoria1:
            try:
                sim1.append(wordvectors.similarity(w_n, w))
            except:
                not_in_we.append(w_n)

        for w in categoria2:
            try:
                sim2.append(wordvectors.similarity(w_n, w))
            except:
                not_in_we.append(w_n)

        for w in categoria3:
            try:
                sim3.append(wordvectors.similarity(w_n, w))
            except:
                not_in_we.append(w_n)

    sim0 = np.mean(sim0)
    sim1 = np.mean(sim1)
    sim2 = np.mean(sim2)
    sim3 = np.mean(sim3)

    return sim0, sim1, sim2, sim3, not_in_we

In [17]:
def centroide_noticia(palabras, dims=30):
    vectores = []
    for w in palabras:
        try:
            vectores.append(wordvectors[w])
        except:
            pass
        
    vectores = np.matrix(vectores)

    return vectores.median(axis=0).tolist()[0]

In [7]:
s0, s1, s2, s3, l = similitud_categorias(categoria3)
print("Similitud categoria 0:", s0)
print("Similitud categoria 1:", s1)
print("Similitud categoria 2:", s2)
print("Similitud categoria 3:", s3)
print('Palabras no en word embedding:', l)

Similitud categoria 0: 0.47152242
Similitud categoria 1: 0.46367338
Similitud categoria 2: 0.4049204
Similitud categoria 3: 0.5917593
Palabras no en word embedding: []


In [18]:
#category=[]
#no_embedding=[]
centroide=[]
for notice in tqdm(data["text_for_embedding"]):
    palabras = word_tokenize(notice)
    #s0, s1, s2, s3, l = similitud_categorias(palabras)
    #max_value=[s0, s1, s2, s3].index(max([s0, s1, s2, s3]))
    #category.append(max_value)
    #no_embedding.append(set(l))
    centroide.append(centroide_noticia(palabras))


0%|          | 0/100640 [00:00<?, ?it/s]


AttributeError: 'matrix' object has no attribute 'median'

In [32]:
dfcat=pd.DataFrame(category)
dfcat.to_csv("category.csv",index=False)

In [34]:
dfwnoembedding=pd.DataFrame(no_embedding)
dfwnoembedding.to_csv("not_embeddingw.csv",encoding="utf-8-sig",index=False)

In [35]:
dfcentroide=pd.DataFrame(centroide)
dfcentroide.to_csv("centroide.csv",index=False)

In [37]:
data["category_bl"]=category


In [39]:
data["no_embedding_words"]=no_embedding
data["centroide"]=centroide

In [40]:
data

titulo  \
0       Cerca de ocho toneladas de coca del Clan del G...   
1       Capturado alias ‘Arturo’, segundo cabecilla de...   
2       Explicaron el traslado de cuerpos posiblemente...   
3       Sigue la guerra verde: ataque a familia de esm...   
4       Investigan caso de recluso amarrado y golpeado...   
...                                                   ...   
100635   Hallan cuerpo de turista que cayó al río Saldaña   
100636  Desmantelan Bacrim dentro del Ejército en el T...   
100637  Continúa ola delincuencial en Mariquita: Asesi...   
100638             Arteaga fue hallado en el río Chipalo    
100639  Dos motociclistas mueren en accidentes de trán...   

                                                   cuerpo  \
0       En una operación de la Policía Nacional y la A...   
1       Sería el encargado de organizar esta estructur...   
2       Hace unos días la ‘Ciudad de las Acacias’ cono...   
3       Familiares de Fray Genaro Cortés Salinas, el c...   
4       Aún se trata de esclarecer las circunstancias ...   
...                                                   ...   
100635  Mediante intensas búsquedas por parte de los o...   
100636  Mediante la operación militar denominada Troya...   
100637  Los hechos se registraron en horas de la tarde...   
100638  Consternado quedó uno de los habitantes de la ...   
100639  Con una buseta El primer caso ocurrió en el ki...   

          fecha_publicacion          diario  \
0       2020-07-01 17:43:00  diariodelcauca   
1       2020-07-01 18:40:00  diariodelcauca   
2       2020-07-01 18:42:00  diariodelcauca   
3       2020-07-01 19:21:00  diariodelcauca   
4       2020-07-02 08:42:00  diariodelcauca   
...                     ...             ...   
100635  2012-03-20 13:45:00      elnuevodia   
100636  2012-03-15 14:40:00      elnuevodia   
100637  2012-03-17 04:00:00      elnuevodia   
100638  2012-04-27 04:00:00      elnuevodia   
100639  2012-03-19 04:03:00      elnuevodia   

                                                      url  page  year  month  \
0       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
1       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
2       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
3       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
4       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
...                                                   ...   ...   ...    ...   
100635  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100636  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100637  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100638  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      4   
100639  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   

        week                                                 id  long_cuerpo  \
0         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          225   
1         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          420   
2         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          488   
3         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          371   
4         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          145   
...      ...                                                ...          ...   
100635    12  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          359   
100636    11  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...         1156   
100637    11  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          292   
100638    17  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          328   
100639    12  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          266   

                                           pre_clean_text  \
0       cerca ocho toneladas coca cla

In [41]:
data.to_csv("data_featuring_all.txt",sep="|",index=False)

In [42]:
data1 = pd.read_csv('data_featuring_all.txt', sep='|')

In [43]:
data1

titulo  \
0       Cerca de ocho toneladas de coca del Clan del G...   
1       Capturado alias ‘Arturo’, segundo cabecilla de...   
2       Explicaron el traslado de cuerpos posiblemente...   
3       Sigue la guerra verde: ataque a familia de esm...   
4       Investigan caso de recluso amarrado y golpeado...   
...                                                   ...   
100635   Hallan cuerpo de turista que cayó al río Saldaña   
100636  Desmantelan Bacrim dentro del Ejército en el T...   
100637  Continúa ola delincuencial en Mariquita: Asesi...   
100638             Arteaga fue hallado en el río Chipalo    
100639  Dos motociclistas mueren en accidentes de trán...   

                                                   cuerpo  \
0       En una operación de la Policía Nacional y la A...   
1       Sería el encargado de organizar esta estructur...   
2       Hace unos días la ‘Ciudad de las Acacias’ cono...   
3       Familiares de Fray Genaro Cortés Salinas, el c...   
4       Aún se trata de esclarecer las circunstancias ...   
...                                                   ...   
100635  Mediante intensas búsquedas por parte de los o...   
100636  Mediante la operación militar denominada Troya...   
100637  Los hechos se registraron en horas de la tarde...   
100638  Consternado quedó uno de los habitantes de la ...   
100639  Con una buseta El primer caso ocurrió en el ki...   

          fecha_publicacion          diario  \
0       2020-07-01 17:43:00  diariodelcauca   
1       2020-07-01 18:40:00  diariodelcauca   
2       2020-07-01 18:42:00  diariodelcauca   
3       2020-07-01 19:21:00  diariodelcauca   
4       2020-07-02 08:42:00  diariodelcauca   
...                     ...             ...   
100635  2012-03-20 13:45:00      elnuevodia   
100636  2012-03-15 14:40:00      elnuevodia   
100637  2012-03-17 04:00:00      elnuevodia   
100638  2012-04-27 04:00:00      elnuevodia   
100639  2012-03-19 04:03:00      elnuevodia   

                                                      url  page  year  month  \
0       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
1       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
2       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
3       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
4       https://diariodelcauca.com.co/noticias/judicia...     3  2020      7   
...                                                   ...   ...   ...    ...   
100635  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100636  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100637  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   
100638  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      4   
100639  https://www.elnuevodia.com.co/nuevodia/actuali...    -1  2012      3   

        week                                                 id  long_cuerpo  \
0         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          225   
1         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          420   
2         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          488   
3         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          371   
4         26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...          145   
...      ...                                                ...          ...   
100635    12  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          359   
100636    11  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...         1156   
100637    11  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          292   
100638    17  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          328   
100639    12  aHR0cHM6Ly93d3cuZWxudWV2b2RpYS5jb20uY28vbnVldm...          266   

                                           pre_clean_text  \
0       cerca ocho toneladas coca cla

In [2]:
data = pd.read_csv('data_featuring_all.txt', sep='|')

In [3]:
data.head()

titulo  \
0  Cerca de ocho toneladas de coca del Clan del G...   
1  Capturado alias ‘Arturo’, segundo cabecilla de...   
2  Explicaron el traslado de cuerpos posiblemente...   
3  Sigue la guerra verde: ataque a familia de esm...   
4  Investigan caso de recluso amarrado y golpeado...   

                                              cuerpo    fecha_publicacion  \
0  En una operación de la Policía Nacional y la A...  2020-07-01 17:43:00   
1  Sería el encargado de organizar esta estructur...  2020-07-01 18:40:00   
2  Hace unos días la ‘Ciudad de las Acacias’ cono...  2020-07-01 18:42:00   
3  Familiares de Fray Genaro Cortés Salinas, el c...  2020-07-01 19:21:00   
4  Aún se trata de esclarecer las circunstancias ...  2020-07-02 08:42:00   

           diario                                                url  page  \
0  diariodelcauca  https://diariodelcauca.com.co/noticias/judicia...     3   
1  diariodelcauca  https://diariodelcauca.com.co/noticias/judicia...     3   
2  diariodelcauca  https://diariodelcauca.com.co/noticias/judicia...     3   
3  diariodelcauca  https://diariodelcauca.com.co/noticias/judicia...     3   
4  diariodelcauca  https://diariodelcauca.com.co/noticias/judicia...     3   

   year  month  week                                                 id  \
0  2020      7    26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...   
1  2020      7    26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...   
2  2020      7    26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...   
3  2020      7    26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...   
4  2020      7    26  aHR0cHM6Ly9kaWFyaW9kZWxjYXVjYS5jb20uY28vbm90aW...   

   long_cuerpo                                     pre_clean_text  \
0          225  cerca ocho toneladas coca clan golfo cayeron o...   
1          420  capturado alias arturo segundo cabecilla disid...   
2          488  explicaron traslado cuerpos posiblemente conta...   
3          371  sigue guerra verde ataque familia esmeraldero ...   
4          145  investigan caso recluso amarrado golpeado pabe...   

                                          clean_text       municipios  \
0  cerc ocho tonel clan golf cayeron operacion co...  colon|cartagena   
1  captur ali cabecill disident tolim vide encarg...      marquetalia   
2  explic trasl cuerp posibl contagi cremacion gi...         girardot   
3  sig ataqu famili esmeralder brutal asesin fami...           boyaca   
4  investig cas reclus amarr golp pabellon psiqui...         medellin   

             departamentos                                 text_for_embedding  \
0  putumayo|narino|bolivar  cerca ocho toneladas clan golfo cayeron operac...   
1                   tolima  capturado alias cabecilla disidencias tolima v...   
2                   bogota  explicaron traslado cuerpos posiblemente conta...   
3                   boyaca  sigue ataque familia esmeraldero brutalmente a...   
4                antioquia  investigan caso recluso amarrado golpeado pabe...   

   category_bl                                 no_embedding_words  \
0            2                                         {'caolin'}   
1            1  {'extorsionando', 'disidencias', 'planadas', '...   
2            0  {'cremados', 'velación', 'tocaima', 'anapoima'...   
3            0  {'pauna', 'amarrándolos', 'yendry', 'borbur', ...   
4            0                               {'buelvas', 'inpec'}   

                                           centroide  
0  [-0.4902389645576477, 0.25123387575149536, -0....  
1  [-0.5124386548995972, 0.2755158245563507, -0.2...  
2  [-0.4598069190979004, 0.1777292937040329, -0.0...  
3  [-0.5200567245483398, 0.02460481785237789, -0....  
4  [-0.48859935998916626, 0.1494164913892746, -0....

In [83]:
newdf = pd.DataFrame()

for i in range(30):
    newdf['x'+str(i)] = data['centroide'].apply(lambda x: float(x.split()[i].replace(',', '').replace('[','').replace(']','')))

In [84]:
newdf

x0        x1        x2        x3        x4        x5        x6  \
0      -0.490239  0.251234 -0.197953  0.122675  0.267247 -0.080400  0.066097   
1      -0.512439  0.275516 -0.223439 -0.032245  0.185129 -0.085937  0.203179   
2      -0.459807  0.177729 -0.019238 -0.026114  0.201583 -0.003371  0.290821   
3      -0.520057  0.024605 -0.017401 -0.119307  0.136427  0.105272  0.199505   
4      -0.488599  0.149416 -0.077937 -0.225326  0.119072  0.049071  0.190456   
...          ...       ...       ...       ...       ...       ...       ...   
100635 -0.574828  0.102565 -0.000143 -0.028398  0.207506  0.004158  0.247605   
100636 -0.497948  0.182403 -0.178651 -0.013921  0.211534 -0.045284  0.205913   
100637 -0.583044  0.037831 -0.034101  0.047135  0.089029  0.120994  0.161061   
100638 -0.545239  0.120910 -0.022147 -0.053663  0.090680  0.022751  0.255137   
100639 -0.487017  0.154157 -0.070049  0.033138  0.004903  0.026931  0.094704   

              x7        x8        x9  ...       x20       x21       x22  \
0      -0.350871  0.196324  0.234812  ... -0.382104 -0.058037  0.148591   
1      -0.288964  0.052847  0.188725  ... -0.326470 -0.069979  0.201104   
2      -0.270029  0.008518  0.373575  ... -0.310703  0.047098  0.158383   
3      -0.230544  0.032785  0.129187  ... -0.385090  0.138291  0.275069   
4      -0.365790 -0.125753  0.294043  ... -0.382177 -0.028826  0.347018   
...          ...       ...       ...  ...       ...       ...       ...   
100635 -0.217163 -0.026808  0.212479  ... -0.356975  0.075698  0.188584   
100636 -0.278610  0.066301  0.151381  ... -0.405985 -0.043232  0.302125   
100637 -0.265413 -0.034966  0.133147  ... -0.313189  0.035458  0.230425   
100638 -0.214109 -0.037533  0.235663  ... -0.308173  0.127672  0.158731   
100639 -0.219167 -0.042007  0.158197  ... -0.335733  0.149553  0.338193   

             x23       x24       x25       x26       x27       x28       x29  
0       0.200550 -0.307812 -0.131351 -0.616587  0.103161 -0.103242 -0.445323  
1       0.243138 -0.203512  0.008064 -0.377339  0.030938 -0.293356 -0.462980  
2       0.175536 -0.277048 -0.091008 -0.473656  0.039975 -0.230764 -0.530001  
3       0.124719 -0.325559 -0.020599 -0.263561  0.074080 -0.199993 -0.670470  
4       0.187394 -0.206832 -0.286368 -0.399186 -0.165557 -0.416888 -0.538262  
...          ...       ...       ...       ...       ...       ...       ...  
100635  0.080273 -0.328591 -0.150003 -0.401734  0.021623 -0.290790 -0.458389  
100636  0.287562 -0.241723 -0.080554 -0.416404  0.083827 -0.330119 -0.458582  
100637  0.138920 -0.367585  0.001810 -0.273743  0.090299 -0.276134 -0.586379  
100638  0.108351 -0.282920 -0.113405 -0.314155 -0.082236 -0.142156 -0.682567  
100639  0.314707 -0.255435 -0.239554 -0.418305 -0.045954 -0.286229 -0.674647  

[100640 rows x 30 columns]

In [85]:
cols = ['x'+str(i) for i in range(30)]

In [92]:
tsne = manifold.TSNE(n_components=3, init='random',
                         random_state=0, perplexity=50)
Y = tsne.fit_transform(newdf[cols].values)

In [109]:
dfTSNE=pd.DataFrame(Y)
dfTSNE.to_csv("TSNE.csv",index=False)

In [3]:
dfY = pd.read_csv('TSNE.csv')

plt.figure(figsize=(15,15))
fig = px.scatter_3d(dfY, x='0', y='1', z='2', color = data.category_bl)

<Figure size 1080x1080 with 0 Axes>

In [4]:
fig.show()

In [11]:
#centro=[]
for notice in tqdm(categoria3):
    palabras = word_tokenize(notice)
    #s0, s1, s2, s3, l = similitud_categorias(palabras)
    #max_value=[s0, s1, s2, s3].index(max([s0, s1, s2, s3]))
    #category.append(max_value)
    #no_embedding.append(set(l))
    centro.append(centroide_noticia(palabras))

100%|██████████| 9/9 [00:00<00:00, 9017.85it/s]


In [16]:
categoria0

['homicidio',
 'masacre',
 'secuestro',
 'tortura',
 'desplazamiento',
 'forzado',
 'confinamiento',
 'accidente',
 'mina',
 'atentado',
 'reclutamiento',
 'violencia',
 'sexual',
 'ataque',
 'indiscriminado',
 'bienes',
 'civiles']